In [1]:
import ctranslate2
import librosa
from transformers import WhisperProcessor   # type: ignore
from IPython.display import Audio
# from whisper import load_audio, pad_or_trim
import numpy as np
import torch
import ffmpeg
import faster_whisper
from whisper_medium_fp16_transformers import load_audio, pad_or_trim

import os
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

2023-07-08 00:26:34.543244: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [9]:
processor = WhisperProcessor.from_pretrained("whisper_medium_int8_ct2")
model = ctranslate2.models.Whisper("whisper_medium_int8_ct2", device="cuda")

In [12]:
processor = WhisperProcessor.from_pretrained("whisper_medium_int8_float16_ct2")
model = ctranslate2.models.Whisper("whisper_medium_int8_float16_ct2", device="cuda")

In [5]:
# Compute the features of the first 30 seconds of audio..
audio = load_audio("../../audios/song_hi.wav", start_time=0)
# audio = pad_or_trim(audio)

inputs = processor(audio, return_tensors="np", sampling_rate=16000)
features = ctranslate2.StorageView.from_array(inputs.input_features)
Audio(audio, rate=16000)

In [13]:
# Detect the language.
# results = model.detect_language(features)
# language, probability = results[0][0]
# print("Detected language %s with probability %f" % (language, probability))
language = "<|hi|>"
# Describe the task in the prompt.
# See the prompt format in https://github.com/openai/whisper.
prompt = processor.tokenizer.convert_tokens_to_ids(
    [
        "<|startoftranscript|>",
        language,
        "<|transcribe|>",
        # "<|notimestamps|>",  # Remove this token to generate timestamps.
    ]
)

# Run generation for the 30-second window.
results = model.generate(features, prompts=[prompt], asynchronous=False, beam_size = 1, return_no_speech_prob = False)
# print(results)
# transcription = processor.batch_decode(results[0].sequences_ids, skip_special_tokens=True, )
# print(transcription)
transcription = processor.decode(results[0].sequences_ids[0], skip_special_tokens=True,)
print(transcription)

 क्यू होना ही है तुमसे ही दिन होता है सुर्मई शाम आती है तुमसे ही तुमसे ही हर गडी सासाती है जिन्दगी कहलाती है तुमसे ही तुमसे ही
